In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import string
import re
import random

In [2]:
df = pd.read_csv('datasets/other_data/conversation.csv')
df.head()

Unnamed: 0                             question  \
0           0               hi, how are you doing?   
1           1        i'm fine. how about yourself?   
2           2  i'm pretty good. thanks for asking.   
3           3    no problem. so how have you been?   
4           4     i've been great. what about you?   

                                     answer  
0             i'm fine. how about yourself?  
1       i'm pretty good. thanks for asking.  
2         no problem. so how have you been?  
3          i've been great. what about you?  
4  i've been good. i'm in school right now.

In [3]:
df.shape

(3725, 3)

## Text Cleaning

In [4]:
# Generate a n sized randomly selected chunk from a series
random_string = lambda a,n: ' '.join(a.sample(n, replace=False))
# Gives the vocabulary from a string.
vocab = lambda s: sorted(list(set(s)))
# Cleans a string so it only has english chars and white spaces. 
pattern = r'[^A-Za-z\s]'
clean_str = lambda s: re.sub(pattern, '', s).lower()
# Removes a specific set of characters from a string.
remove_chars = lambda t,c: re.compile('|'.join(map(re.escape, c))).sub(' ', t)
# Modify a string into n sized chunks
chunkify = lambda s,n: [s[i:i+4].strip() for i in range(0, len(s), n)]

In [5]:
## INITIAL TEXT DATA
# body_texts = random_string(df['Body/Text'],4000)
body_texts = ' '.join(df['question'])
print(vocab(body_texts))

[' ', '!', '"', '$', '&', "'", ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', '?', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', 'Â', '—', '…']


In [6]:
## DOING REFERENCE CLEANING
body_texts = clean_str(body_texts)
print(vocab(body_texts))

[' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']


In [7]:
## DOING REFERENCE CLEANING
body_texts = remove_chars(body_texts,['\xa0','\u2002','\u2005','\u200a','\t','\n','\r'])
print(vocab(body_texts))

[' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']


In [8]:
body_texts = [i for i in body_texts.split() if len(i) < 20]
# body_texts = chunkify(body_texts,3)
print(body_texts)

['hi', 'how', 'are', 'you', 'doing', 'im', 'fine', 'how', 'about', 'yourself', 'im', 'pretty', 'good', 'thanks', 'for', 'asking', 'no', 'problem', 'so', 'how', 'have', 'you', 'been', 'ive', 'been', 'great', 'what', 'about', 'you', 'ive', 'been', 'good', 'im', 'in', 'school', 'right', 'now', 'what', 'school', 'do', 'you', 'go', 'to', 'i', 'go', 'to', 'pcc', 'do', 'you', 'like', 'it', 'there', 'its', 'okay', 'its', 'a', 'really', 'big', 'campus', 'good', 'luck', 'with', 'school', 'hows', 'it', 'going', 'im', 'doing', 'well', 'how', 'about', 'you', 'never', 'better', 'thanks', 'so', 'how', 'have', 'you', 'been', 'lately', 'ive', 'actually', 'been', 'pretty', 'good', 'you', 'im', 'actually', 'in', 'school', 'right', 'now', 'which', 'school', 'do', 'you', 'attend', 'im', 'attending', 'pcc', 'right', 'now', 'are', 'you', 'enjoying', 'it', 'there', 'its', 'not', 'bad', 'there', 'are', 'a', 'lot', 'of', 'people', 'there', 'good', 'luck', 'with', 'that', 'how', 'are', 'you', 'doing', 'today', '

In [9]:
vocab_size = len(vocab(body_texts))
vocab_size

2337

In [10]:
# data = {}
# for i in set(body_texts):
#     data[i] = body_texts.count(i)
    
# # Sort the dictionary by values in descending order and select the top 20 items
# sorted_data = sorted(data.items(), key=lambda x: x[1], reverse=True)[:20]

# # Extract the keys and values from the sorted data
# keys = [item[0] for item in sorted_data]
# values = [item[1] for item in sorted_data]

# # Create a bar chart
# plt.bar(keys, values)

# # Add labels and title
# plt.xlabel('Words')
# plt.ylabel('Occurrences')
# plt.title('Top 20 Words')

# # Rotate x-axis labels for better readability if needed
# plt.xticks(rotation=45)

# # Display the chart
# plt.show()

## Training Model

In [11]:
import torch
import torch.nn as nn
from torch.nn import functional as F

In [12]:
# hyperparameters
batch_size = 32 # how many independent sequences will we process in parallel?
block_size = 16 # what is the maximum context length for predictions?
hidden_size = 8
max_iters = 100000
eval_interval = 10000
learning_rate = 0.01
device = 'cuda' if torch.cuda.is_available() else 'cpu'
eval_iters = 1000

In [13]:
# create a mapping from characters to integers
stoi = { ch:i for i,ch in enumerate(vocab(body_texts)) }
itos = { i:ch for i,ch in enumerate(vocab(body_texts)) }
encode = lambda s: [stoi[c] for c in s] # encoder: take a string, output a list of integers
decode = lambda l: ' '.join([itos[i] for i in l]) # decoder: take a list of integers, output a string

In [14]:
# Train and test splits
data = torch.tensor(encode(body_texts), dtype=torch.long)
n = int(0.9*len(data)) # first 90% will be train, rest val
train_data = data[:n]
val_data = data[n:]

In [15]:
# data loading
def get_batch(split):
    # generate a small batch of data of inputs x and targets y
    data = train_data if split == 'train' else val_data
    ix = torch.randint(len(data) - block_size, (batch_size,))
    x = torch.stack([data[i:i+block_size] for i in ix])
    y = torch.stack([data[i+1:i+block_size+1] for i in ix])
    x, y = x.to(device), y.to(device)
    return x, y

@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iters)
        for k in range(eval_iters):
            X, Y = get_batch(split)
            logits, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    model.train()
    return out

In [16]:
class SelfAttention(nn.Module):
    def __init__(self, hidden_size):
        super().__init__()
        self.hidden_size = hidden_size
        self.query = nn.Linear(hidden_size, hidden_size)
        self.key = nn.Linear(hidden_size, hidden_size)
        self.value = nn.Linear(hidden_size, hidden_size)

    def forward(self, inputs):
        query = self.query(inputs)
        key = self.key(inputs)
        value = self.value(inputs)

        attn_weights = torch.matmul(query, key.transpose(-2, -1))
        attn_weights = F.softmax(attn_weights, dim=-1)
        attended = torch.matmul(attn_weights, value)

        return attended

In [17]:
# super simple bigram model
class BigramLanguageModel(nn.Module):

    def __init__(self, vocab_size):
        super().__init__()
        # each token directly reads off the logits for the next token from a lookup table
        self.token_embedding_table = nn.Embedding(vocab_size, vocab_size)

    def forward(self, idx, targets=None):

        # idx and targets are both (B,T) tensor of integers
        logits = self.token_embedding_table(idx) # (B,T,C)

        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B*T, C)
            targets = targets.view(B*T)
            loss = F.cross_entropy(logits, targets)

        return logits, loss

    def generate(self, idx, max_new_tokens):
        # idx is (B, T) array of indices in the current context
        for _ in range(max_new_tokens):
            # get the predictions
            logits, loss = self(idx)
            # focus only on the last time step
            logits = logits[:, -1, :] # becomes (B, C)
            # apply softmax to get probabilities
            probs = F.softmax(logits, dim=-1) # (B, C)
            # sample from the distribution
            idx_next = torch.multinomial(probs, num_samples=1) # (B, 1)
            # append sampled index to the running sequence
            idx = torch.cat((idx, idx_next), dim=1) # (B, T+1)
        return idx

In [18]:
class BigramLanguageModelAttention(nn.Module):
    def __init__(self, vocab_size, hidden_size):
        super().__init__()
        self.vocab_size = vocab_size
        self.hidden_size = hidden_size

        self.token_embedding_table = nn.Embedding(vocab_size, hidden_size)
        self.self_attention = SelfAttention(hidden_size)
        self.fc = nn.Linear(hidden_size, vocab_size)

    def forward(self, idx, targets=None):
        embeddings = self.token_embedding_table(idx)  # (B, T, hidden_size)
        attended = self.self_attention(embeddings)  # (B, T, hidden_size)

        logits = self.fc(attended)  # (B, T, vocab_size)

        if targets is None:
            loss = None
        else:
            B, T, _ = logits.shape
            logits = logits.view(B * T, -1)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)

        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            logits, _ = self(idx)
            last_logits = logits[:, -1, :]  # (B, vocab_size)
            probs = F.softmax(last_logits, dim=-1)  # (B, vocab_size)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

    def compute_reward(self, idx, targets):
        _, loss = self(idx, targets)
        reward = loss.item()  # Negative loss as the reward
        return reward

In [44]:
model = BigramLanguageModelAttention(vocab_size,hidden_size)
m = model.to(device)
# create a PyTorch optimizer
optimizer = torch.optim.AdamW(model.parameters(), lr=learning_rate)

In [20]:
# Basic Loop
# for iter in range(max_iters):

#     # every once in a while evaluate the loss on train and val sets
#     if iter % eval_interval == 0:
#         losses = estimate_loss()
#         print(f"step {iter}: train loss {losses['train']:.4f}, val loss {losses['val']:.4f}")

#     # sample a batch of data
#     xb, yb = get_batch('train')

#     # evaluate the loss
#     logits, loss = model(xb, yb)
#     optimizer.zero_grad(set_to_none=True)
#     loss.backward()
#     optimizer.step()

In [45]:
# Reward Loop
for iter in range(max_iters):
    # Every once in a while, evaluate the loss on train and val sets
    if iter % eval_interval == 0:
        losses = estimate_loss()
        print(f"Step {iter}: train loss {losses['train']:.4f}, val loss {losses['val']:.4f}")

    # Sample a batch of data
    xb, yb = get_batch('train')
    print (xb,yb)
    logits, loss = model(xb, yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()

    # Update the model using policy gradients
#     rewards = model.compute_reward(xb, yb)
#     optimizer.zero_grad()
#     logits, _ = model(xb)
#     log_probs = F.log_softmax(logits, dim=-1)
#     rewards_tensor = torch.tensor(rewards)  # Convert rewards to a tensor
#     policy_loss = -(log_probs * rewards_tensor.unsqueeze(0)).mean()  # Unsqueeze along dimension 0
#     policy_loss.backward()
#     optimizer.step()
torch.save('generative_model.pt')

Step 0: train loss 7.7819, val loss 7.7686
tensor([[ 749,   38, 2028,  ..., 1730, 2320, 2028],
        [  29, 2259, 1017,  ..., 2245, 2079,  348],
        [ 979,  285,   55,  ..., 2325,  876, 2079],
        ...,
        [1290, 2079, 1689,  ...,  284,  894, 1208],
        [2025,  973,  799,  ..., 2253, 1356,  964],
        [ 822, 1017, 2329,  ...,  641, 1017, 1930]]) tensor([[  38, 2028, 1249,  ..., 2320, 2028, 2290],
        [2259, 1017, 2025,  ..., 2079,  348,   80],
        [ 285,   55,  727,  ...,  876, 2079, 1984],
        ...,
        [2079, 1689, 1249,  ...,  894, 1208, 2259],
        [ 973,  799,  778,  ..., 1356,  964,  554],
        [1017, 2329, 1200,  ..., 1017, 1930, 2027]])
tensor([[1286,  746,  871,  ..., 1908, 2025, 2209],
        [2209,  941,   55,  ...,  973, 1322, 1022],
        [1653, 1017, 1303,  ...,  554,  876,   67],
        ...,
        [1480, 2028,  924,  ...,  910, 1376, 1022],
        [1689,  630,  749,  ..., 2201, 1208, 2079],
        [2034, 1020, 2263,  ...,

tensor([[2330, 2310,  964,  ..., 1118, 1900,  749],
        [2242, 1058, 1258,  ..., 2320, 1022, 1354],
        [1570,  544, 1186,  ...,  813, 2079, 2028],
        ...,
        [1857, 1340,   90,  ..., 1279,  946,   55],
        [2329,  271, 2236,  ...,   16, 1448,  340],
        [1958, 2236, 2326,  ..., 2079, 1408,  371]]) tensor([[2310,  964, 1967,  ..., 1900,  749, 2128],
        [1058, 1258, 1340,  ..., 1022, 1354,  639],
        [ 544, 1186, 1020,  ..., 2079, 2028,  152],
        ...,
        [1340,   90,  372,  ...,  946,   55, 2216],
        [ 271, 2236, 1340,  ..., 1448,  340, 2079],
        [2236, 2326,  179,  ..., 1408,  371,  397]])
tensor([[ 964,  290, 1873,  ..., 2046, 2040,  179],
        [1773, 2253, 1356,  ..., 1290, 2079, 1689],
        [2214,    0, 1158,  ..., 1210,   80, 2325],
        ...,
        [ 964, 1693, 2325,  ..., 2034, 2222, 2237],
        [ 970, 2222,  554,  ..., 1335,  522,  880],
        [2259, 1322, 1746,  ..., 1833,  964,   97]]) tensor([[ 290, 1873,  

tensor([[ 775, 2242, 2070,  ...,  901,  686, 1992],
        [2322,  880,   97,  ..., 1017, 1020, 1022],
        [2081, 2236, 1750,  ..., 1407, 1894, 2028],
        ...,
        [2328,  522, 2325,  ..., 2071,   46, 2259],
        [1020,  523,  797,  ...,  151, 1438,  152],
        [2201, 2079, 1478,  ..., 2320,  880, 1179]]) tensor([[2242, 2070,  544,  ...,  686, 1992, 1512],
        [ 880,   97, 1208,  ..., 1020, 1022, 1360],
        [2236, 1750, 1530,  ..., 1894, 2028, 1007],
        ...,
        [ 522, 2325,  884,  ...,   46, 2259,  522],
        [ 523,  797, 1833,  ..., 1438,  152, 2226],
        [2079, 1478,  749,  ...,  880, 1179, 2028]])
tensor([[1130, 2028, 1018,  ..., 2037,  765,  964],
        [ 771,  540, 2325,  ...,  439,  813, 2079],
        [ 677,  979,    0,  ...,    0, 1658,  964],
        ...,
        [2242, 2330,  817,  ...,  964, 2299, 1590],
        [ 967, 2250,  540,  ...,  880,  540, 1020],
        [ 813, 2151,  775,  ...,  840, 2325,  540]]) tensor([[2028, 1018, 1

tensor([[ 649, 2222,  290,  ..., 1020, 2213,    0],
        [1354, 1020, 2330,  ..., 1022,  533,  158],
        [1130,  949,  380,  ...,  151, 2028,  751],
        ...,
        [ 964, 1996, 1020,  ..., 1279,  236, 1017],
        [1020, 2209, 1130,  ...,  114, 1249, 1017],
        [1372,   60, 2242,  ..., 1020, 2028, 1994]]) tensor([[2222,  290,   21,  ..., 2213,    0, 1739],
        [1020, 2330,  456,  ...,  533,  158,  973],
        [ 949,  380, 2028,  ..., 2028,  751, 1695],
        ...,
        [1996, 1020, 2245,  ...,  236, 1017,   39],
        [2209, 1130,  169,  ..., 1249, 1017, 1020],
        [  60, 2242,  619,  ..., 2028, 1994, 1596]])
tensor([[2028,  207, 1279,  ..., 1760,   80, 1755],
        [2247, 1017,  880,  ...,  425, 1308,  964],
        [1298,  293, 2320,  ..., 1833, 2242,  540],
        ...,
        [1290, 2079,  265,  ...,   60,   80,  783],
        [   0,  956, 1298,  ...,  964,  554, 1069],
        [2263,  151, 2142,  ..., 1237,  964, 2046]]) tensor([[ 207, 1279,  

tensor([[2154,    2,    0,  ..., 1354,    0, 2113],
        [ 547,   55, 2035,  ..., 1561, 2028, 1294],
        [  80, 2325,  817,  ..., 2209, 1308, 2289],
        ...,
        [ 774, 2329, 1036,  ...,  540, 2276, 1020],
        [ 727, 1004, 2028,  ..., 1984,  296, 1340],
        [2052, 1257,  973,  ..., 1896,  101, 1335]]) tensor([[   2,    0,  153,  ...,    0, 2113, 1927],
        [  55, 2035,   80,  ..., 2028, 1294,  554],
        [2325,  817, 2079,  ..., 1308, 2289, 2242],
        ...,
        [2329, 1036, 1019,  ..., 2276, 1020, 1631],
        [1004, 2028, 2154,  ...,  296, 1340, 2329],
        [1257,  973,  845,  ...,  101, 1335,  972]])
tensor([[ 979,    0, 2254,  ...,  101, 2247,  540],
        [2209, 1778, 2027,  ..., 2230, 1833,  813],
        [2079, 2046,  839,  ..., 1963, 2213, 2035],
        ...,
        [1635, 2028,  256,  ...,  880, 2285, 1842],
        [2218, 2028, 1371,  ..., 1833,  540,  964],
        [ 265, 2329, 2064,  ..., 1269, 1020, 2263]]) tensor([[   0, 2254, 1

...

tensor([[ 261,  964,  522,  ..., 1366, 2329, 1366],
        [1061,  555,  949,  ..., 2222,  284,  813],
        [  80,   46,  233,  ...,  490,  964, 1693],
        ...,
        [ 798, 2028, 1542,  ..., 1792,  336,  540],
        [2210, 1020, 2027,  ..., 1047, 1186,    0],
        [2032, 1848, 2040,  ..., 1017, 1243,   96]]) tensor([[ 964,  522, 1555,  ..., 2329, 1366, 1019],
        [ 555,  949,    2,  ...,  284,  813, 2079],
        [  46,  233,  979,  ...,  964, 1693, 2325],
        ...,
        [2028, 1542,  233,  ...,  336,  540, 2325],
        [1020, 2027, 2242,  ..., 1186,    0, 2162],
        [1848, 2040,  177,  ..., 1243,   96, 2028]])
tensor([[2201, 2079,  151,  ..., 2222,  797,  856],
        [ 979, 1279,  305,  ..., 1279, 1236,  544],
        [ 261, 2028, 1819,  ...,  964, 2090, 2032],
        ...,
        [ 603, 2079, 1606,  ..., 1375,   95, 2263],
        [1020,  964,  554,  ..., 1230, 1920, 2325],
        [2325, 1302, 2070,  ..., 2196, 2028,  546]]) tensor([[2079,  151,  

tensor([[2325,  964,  876,  ..., 2222, 1771, 1590],
        [ 817, 1233, 1436,  ...,  151,  807, 2242],
        [ 797,  539, 1279,  ...,  949,    2,    0],
        ...,
        [   0, 1470,  851,  ..., 2263, 2325, 1148],
        [1967,  934, 1833,  ..., 1560, 2250,  540],
        [ 109, 2012, 1175,  ...,  431,  703, 1376]]) tensor([[ 964,  876, 2079,  ..., 1771, 1590,  540],
        [1233, 1436,  944,  ...,  807, 2242,    0],
        [ 539, 1279, 2261,  ...,    2,    0, 1466],
        ...,
        [1470,  851,  455,  ..., 2325, 1148,  101],
        [ 934, 1833, 1844,  ..., 2250,  540, 2028],
        [2012, 1175, 1020,  ...,  703, 1376, 2259]])
tensor([[ 749,  894,  964,  ..., 2330, 1636,  257],
        [ 158, 1400,  554,  ..., 2263, 1540, 2325],
        [2209, 2028, 1851,  ...,  312, 2325, 2327],
        ...,
        [1020,  964, 1402,  ..., 1020,  202, 2106],
        [1340, 1329,  949,  ..., 1696,  964, 1290],
        [  80, 2325, 1967,  ..., 1322, 2089, 1269]]) tensor([[ 894,  964,  

tensor([[2171, 1169, 2259,  ..., 1210,  970, 2330],
        [2325,  554, 1130,  ...,   55,  854, 2242],
        [1694, 2025, 2028,  ...,  554, 2242,  540],
        ...,
        [1478, 2276, 2028,  ...,  979, 2028, 2287],
        [  55, 1601, 1484,  ..., 1766,  308,   80],
        [2038, 1990,    2,  ..., 2325, 1771, 1595]]) tensor([[1169, 2259,  540,  ...,  970, 2330,  817],
        [ 554, 1130, 2079,  ...,  854, 2242, 1058],
        [2025, 2028, 1802,  ..., 2242,  540, 2325],
        ...,
        [2276, 2028, 1053,  ..., 2028, 2287, 2250],
        [1601, 1484,  898,  ...,  308,   80,  485],
        [1990,    2, 1372,  ..., 1771, 1595, 1020]])
tensor([[1020, 2209, 1354,  ..., 1842, 2233, 2325],
        [ 619,  964, 1130,  ...,  964, 1585, 1020],
        [ 779,   55, 1020,  ..., 1350,  837, 2222],
        ...,
        [ 880, 1157, 1020,  ..., 1020,  749, 2325],
        [ 877, 2325, 2107,  ..., 1335, 1350, 2236],
        [1020,   80, 2325,  ...,  523,  876, 2070]]) tensor([[2209, 1354, 1

tensor([[ 143, 2311, 1022,  ..., 2258, 2028,  838],
        [2320, 2035, 1017,  ..., 1022, 1360,    0],
        [2209,  260, 2028,  ...,  837, 1036, 1022],
        ...,
        [   0, 2004, 2006,  ..., 1771,  540, 1846],
        [1303, 1981, 1308,  ..., 2320, 2028, 1075],
        [2079, 1020, 1256,  ..., 2224,    0, 1024]]) tensor([[2311, 1022,    0,  ..., 2028,  838,  141],
        [2035, 1017,  964,  ..., 1360,    0,  443],
        [ 260, 2028, 2257,  ..., 1036, 1022, 2028],
        ...,
        [2004, 2006, 1017,  ...,  540, 1846, 2025],
        [1981, 1308, 1022,  ..., 2028, 1075, 1017],
        [1020, 1256, 1562,  ...,    0, 1024, 2089]])
tensor([[  38, 2038, 2046,  ...,  540, 2325, 2201],
        [2079, 2325, 2089,  ...,  630,  803, 1130],
        [  96, 1208, 2242,  ..., 1352, 2242, 1058],
        ...,
        [1322,  703, 1376,  ..., 1020,  798,    0],
        [2070, 2034,  972,  ...,  622,  964,  554],
        [1635, 2028,  256,  ...,  880, 2285, 1842]]) tensor([[2038, 2046,  

TypeError: save() missing 1 required positional argument: 'f'

In [46]:
import time
context = torch.zeros((1, 1), dtype=torch.long, device=device)
max_new_chars = 100
max_new_words = 20

user_input = clean_str(input("Context Generator, Give context: "))
# user_encoded = encode(user_input) # for chars
user_encoded = encode(user_input.split()) # for words
tensor = torch.tensor(user_encoded, dtype=torch.long, device=device).unsqueeze(0)

generated_text = ""
print("Generated Text:")

# generate from chars
# for _ in range(max_new_chars):
#     res = m.generate(tensor, max_new_tokens=1)[0].tolist()
#     context = torch.cat((tensor, torch.tensor(res[-1:], dtype=torch.long, device=device).unsqueeze(0)), dim=1)
#     generated_word = decode(res[-1:])
#     time.sleep(0.01)
#     generated_text += generated_word
#     if generated_text[-1] == ' ':
#         print(generated_text[:-1], end=' ')
#         generated_text = ''
        
# generate from words
for _ in range(max_new_words):
    res = m.generate(context, max_new_tokens=1)[0].tolist()
    context = torch.cat((context, torch.tensor([res[-1]], dtype=torch.long, device=device).unsqueeze(0)), dim=1)
    generated_word = decode(res[-1:])
    time.sleep(0.01)
    print(generated_word, end=' ')

Context Generator, Give context: hello
Generated Text:
melts have left perfect certain mountains whats cool superbad even found okay when they give want talk ready had talk 

In [39]:
import torch
import torch.nn as nn
from torch.nn import functional as F

# hyperparameters
batch_size = 64 # how many independent sequences will we process in parallel?
block_size = 256 # what is the maximum context length for predictions?
max_iters = 5000
eval_interval = 500
learning_rate = 3e-4
device = 'cuda' if torch.cuda.is_available() else 'cpu'
eval_iters = 200
n_embd = 384
n_head = 6
n_layer = 6
dropout = 0.2
# ------------

class Head(nn.Module):
    """ one head of self-attention """
    def __init__(self, head_size):
        super().__init__()
        self.key = nn.Linear(n_embd, head_size, bias=False)
        self.query = nn.Linear(n_embd, head_size, bias=False)
        self.value = nn.Linear(n_embd, head_size, bias=False)
        self.register_buffer('tril', torch.tril(torch.ones(block_size, block_size)))

        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        # input of size (batch, time-step, channels)
        # output of size (batch, time-step, head size)
        B,T,C = x.shape
        k = self.key(x)   # (B,T,hs)
        q = self.query(x) # (B,T,hs)
        # compute attention scores ("affinities")
        wei = q @ k.transpose(-2,-1) * k.shape[-1]**-0.5 # (B, T, hs) @ (B, hs, T) -> (B, T, T)
        wei = wei.masked_fill(self.tril[:T, :T] == 0, float('-inf')) # (B, T, T)
        wei = F.softmax(wei, dim=-1) # (B, T, T)
        wei = self.dropout(wei)
        # perform the weighted aggregation of the values
        v = self.value(x) # (B,T,hs)
        out = wei @ v # (B, T, T) @ (B, T, hs) -> (B, T, hs)
        return out

class MultiHeadAttention(nn.Module):
    """ multiple heads of self-attention in parallel """

    def __init__(self, num_heads, head_size):
        super().__init__()
        self.heads = nn.ModuleList([Head(head_size) for _ in range(num_heads)])
        self.proj = nn.Linear(head_size * num_heads, n_embd)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim=-1)
        out = self.dropout(self.proj(out))
        return out

class FeedFoward(nn.Module):
    """ a simple linear layer followed by a non-linearity """

    def __init__(self, n_embd):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, 4 * n_embd),
            nn.ReLU(),
            nn.Linear(4 * n_embd, n_embd),
            nn.Dropout(dropout),
        )

    def forward(self, x):
        return self.net(x)

class Block(nn.Module):
    """ Transformer block: communication followed by computation """

    def __init__(self, n_embd, n_head):
        # n_embd: embedding dimension, n_head: the number of heads we'd like
        super().__init__()
        head_size = n_embd // n_head
        self.sa = MultiHeadAttention(n_head, head_size)
        self.ffwd = FeedFoward(n_embd)
        self.ln1 = nn.LayerNorm(n_embd)
        self.ln2 = nn.LayerNorm(n_embd)

    def forward(self, x):
        x = x + self.sa(self.ln1(x))
        x = x + self.ffwd(self.ln2(x))
        return x

class GPTLanguageModel(nn.Module):

    def __init__(self):
        super().__init__()
        # each token directly reads off the logits for the next token from a lookup table
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(n_embd, n_head=n_head) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embd) # final layer norm
        self.lm_head = nn.Linear(n_embd, vocab_size)

        # better init, not covered in the original GPT video, but important, will cover in followup video
        self.apply(self._init_weights)

    def _init_weights(self, module):
        if isinstance(module, nn.Linear):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
            if module.bias is not None:
                torch.nn.init.zeros_(module.bias)
        elif isinstance(module, nn.Embedding):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)

    def forward(self, idx, targets=None):
        B, T = idx.shape

        # idx and targets are both (B,T) tensor of integers
        tok_emb = self.token_embedding_table(idx) # (B,T,C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=device)) # (T,C)
        x = tok_emb + pos_emb # (B,T,C)
        x = self.blocks(x) # (B,T,C)
        x = self.ln_f(x) # (B,T,C)
        logits = self.lm_head(x) # (B,T,vocab_size)

        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B*T, C)
            targets = targets.view(B*T)
            loss = F.cross_entropy(logits, targets)

        return logits, loss

    def generate(self, idx, max_new_tokens):
        # idx is (B, T) array of indices in the current context
        for _ in range(max_new_tokens):
            # crop idx to the last block_size tokens
            idx_cond = idx[:, -block_size:]
            # get the predictions
            logits, loss = self(idx_cond)
            # focus only on the last time step
            logits = logits[:, -1, :] # becomes (B, C)
            # apply softmax to get probabilities
            probs = F.softmax(logits, dim=-1) # (B, C)
            # sample from the distribution
            idx_next = torch.multinomial(probs, num_samples=1) # (B, 1)
            # append sampled index to the running sequence
            idx = torch.cat((idx, idx_next), dim=1) # (B, T+1)
        return idx

model = GPTLanguageModel()
m = model.to(device)
# print the number of parameters in the model
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')
# create a PyTorch optimizer
optimizer = torch.optim.AdamW(model.parameters(), lr=learning_rate)

12.536097 M parameters
